<a href="https://colab.research.google.com/github/DivyaSharma0795/Explainable_AI_Techniques_01/blob/main/Explainable_Techniques_1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# AIPI 590 - XAI | Assignment #02
### Explainable Techniques 01
### Divya Sharma

[![Open In Collab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/DivyaSharma0795/Explainable_AI_Techniques_01/blob/main/Explainable_Techniques_1.ipynb)

# Introduction

This notebook aims to generate **local explanations** for predictions made by the **GPT-2** language model using **SHAP (SHapley Additive ExPlanations)**. SHAP is a powerful, model-agnostic explanation technique based on game theory that helps interpret how individual input features contribute to a model's output.

### Purpose
The goal is to:
- Understand how specific tokens in the input text influence GPT-2's predictions.
- Visualize and interpret the contributions of each token to the model's output.

### Overview
#### **Input**
- The input text used for this analysis is a manually selected sentence:  
  *"In a surprising discovery, scientists found evidence of life on Mars."*
- This input will be processed by GPT-2 to generate predictions for the next tokens.

#### **Model**
- **GPT-2**: A pre-trained transformer-based language model developed by OpenAI. It generates text by predicting the next token in a sequence based on the given input.

#### **Explanation Technique**
- **SHAP (SHapley Additive ExPlanations)**:
  - SHAP values explain the contribution of each input token to GPT-2's predicted output tokens.
  - The framework provides local explanations, enabling us to understand individual predictions in detail.
  - SHAP uses a game-theoretic approach to fairly allocate contributions among features (tokens).

By combining GPT-2 and SHAP, this notebook provides insights into how GPT-2 processes input text and generates output predictions.


# Step 0 - importinng necessary libraries

In [ ]:
pip install transformers shap

In [ ]:
# Importing required libraries for reading data and EDA
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from transformers import AutoModelForCausalLM, AutoTokenizer
import shap


# Step 1 - Load pre-trained GPT-2 model

In [ ]:
model = AutoModelForCausalLM.from_pretrained("gpt2")
tokenizer = AutoTokenizer.from_pretrained("gpt2")

# Step 2 - Data Preparation

In [ ]:
input_text = ["In a surprising discovery, scientists found evidence of life on Mars."]

In [ ]:
tokenized_input = tokenizer(input_text, return_tensors="pt")

# Step 3 - Explanation with SHAP

In [ ]:
# a. Create SHAP Explainer
# Wrap the model and tokenizer for SHAP:
masker = shap.maskers.Text(tokenizer)
explainer = shap.Explainer(model, masker)

In [ ]:
# b. Compute SHAP Values
# Generate SHAP values for the input text:
shap_values = explainer(input_text)


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


  0%|          | 0/156 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:38, 38.48s/it]               


In [ ]:
# c. Visualization
# Visualize the token contributions using SHAP's text plot:
shap.plots.text(shap_values)

### Explanation

Color Coding:

-   Red Tokens: These tokens positively contribute to the model's prediction, pushing the output probability higher.
-   Blue Tokens: These tokens negatively contribute to the model's prediction, pushing the output probability lower.
-   The intensity of the color (darker or lighter shades) represents the magnitude of the contribution. Darker colors indicate stronger influence.

Token Contributions:

-    Each token in the input text is highlighted with a background color based on its SHAP value.
-    Hovering over a token (in interactive environments) may display its exact SHAP value, which quantifies its contribution to the prediction.

Insights from SHAP Values

The visualization helps identify which parts of the input text drive specific predictions, offering transparency into black-box models like GPT-2.

For example, for the input "In a surprising discovery, scientists found evidence of life on Mars.", GPT-2 generates the following output:
"In a surprising discovery , scientists found evidence of life on Mars . The discovery , reported in"

If we highlight the generated token "discovery", we see the pre-existing "discovery", "found", and "of" are contributing the highest in generating the word.
If we highlight the generated token "reported", we see the pre-existing "surprising" and "scientists" are contributing the highest in generating the word, while "evidence" and "Mars" are contributing less towards this word.


In [ ]:
words = shap_values.data[0]  # List of words or tokens
# words.shape
# 13
base_values = shap_values.base_values[0]  # Base values for each token
# base_values.shape
# 20
shap_values_2d = shap_values.values[0]  # SHAP values for each token
# shap_values_2d.shape
# (13, 20)

# Repeat base values for all tokens
base_values_expanded = pd.DataFrame(
    [base_values] * len(words),
    columns=[f"Base Value {i+1}" for i in range(len(base_values))]
)

# Create DataFrame
shap_df = pd.DataFrame(
    shap_values_2d,
    columns=[f"SHAP Value {i+1}" for i in range(shap_values_2d.shape[1])]
)
shap_df.insert(0, "Word", words)

# Display DataFrame
shap_df


Word  SHAP Value 1  SHAP Value 2  SHAP Value 3  SHAP Value 4  \
0            In     -0.318074      0.530199      0.868294      0.821443   
1             a      0.130948      1.236026      0.926698      0.215486   
2    surprising     -0.250731     -0.181811      3.891352      1.183473   
3     discovery     -0.192914     -0.314043      0.441959      4.144674   
4             ,      0.180433     -0.176387     -0.109427      0.272227   
5    scientists     -0.264525      0.586158      1.318714      1.276394   
6         found      0.457567      0.173212     -0.076992      0.900027   
7      evidence     -0.605849     -0.073921      0.143237      0.194327   
8            of     -0.516361      0.082170      0.174810      0.348031   
9          life     -0.394081     -0.190937     -0.421398     -0.117452   
10           on     -0.212275      0.034415      0.134849      0.106985   
11         Mars     -1.284871      0.255294      0.223619      0.301920   
12            .      1.292551     -0.104922     -0.370299     -0.163169   

    SHAP Value 5  SHAP Value 6  SHAP Value 7  SHAP Value 8  SHAP Value 9  ...  \
0       0.225699      0.186119      0.704452      0.363039      0.503322  ...   
1       0.450116      0.352859      0.101434     -0.015088     -0.120316  ...   
2       0.172290      0.591540      0.352248      0.068120      0.110034  ...   
3       0.573469     -0.297042      0.794070      0.518489      0.345907  ...   
4       3.024682      0.288605      0.468728      0.037130      0.084995  ...   
5       0.866861      4.314285      1.230593      0.353213      0.425919  ...   
6       0.257224      0.208558      2.745759      1.252167      0.891536  ...   
7       0.033846      0.006023     -0.108711      3.302532      0.629125  ...   
8       0.420026     -0.053614      0.192353      0.701705      1.925422  ...   
9      -0.335233      0.120701     -0.265967     -0.199870     -0.240625  ...   
10      0.167412     -0.046461      0.102232      0.432422      0.333935  ...   
11     -0.403995      0.441235     -0.280748     -0.245730     -0.267566  ...   
12      0.035134     -0.455257     -0.084757     -0.335450      0.132793  ...   

    SHAP Value 24  SHAP Value 25  SHAP Value 26  SHAP Value 27  SHAP Value 28  \
0        0.078563      -0.012602       0.116590       0.040080       0.052391   
1       -0.024121      -0.021065      -0.004476       0.015618       0.056268   
2        0.021051       0.012569       0.018265       0.058260       0.003770   
3        0.018090       0.061698      -0.034154       0.061229      -0.033617   
4       -0.011445      -0.037750       0.021833      -0.017039       0.002234   
5       -0.008107      -0.022194      -0.030824      -0.037992       0.079531   
6        0.047278      -0.006291       0.026321      -0.000421      -0.019145   
7        0.066015       0.027691       0.003459      -0.094567       0.012059   
8       -0.029164       0.024269       0.013282      -0.018803      -0.012169   
9       -0.004164      -0.033221       0.045109       0.033747      -0.008113   
10      -0.020547       0.006661      -0.008570       0.023320       0.021324   
11       0.031003      -0.009018      -0.112357       0.092730      -0.009712   
12       0.037279       0.006076      -0.051014       0.008969       0.004649   

    SHAP Value 29  SHAP Value 30  SHAP Value 31  SHAP Value 32  SHAP Value 33  
0        0.117869       0.012461      -0.030633      -0.023710       0.005201  
1        0.046381       0.044336      -0.058005       0.001713      -0.063096  
2        0.028299       0.023260       0.007004       0.015981      -0.054927  
3       -0.091838       0.043639      -0.121983      -0.018921       0.125963  
4        0.027725       0.021206       0.006006      -0.006120       0.099905  
5       -0.020317       0.074342      -0.061313      -0.077484       0.036507  
6       -0.016357      -0.003866       0.012956      -0.004381      -0.062882  
7        0.013161      -0.046512      -0.060667   

### Additional Examples

### Example 2: "I am a data science student at Duke"

In [ ]:
input_text = ["I am a data science student at Duke."]
tokenized_input = tokenizer(input_text, return_tensors="pt")
masker = shap.maskers.Text(tokenizer)
explainer = shap.Explainer(model, masker)
shap_values = explainer(input_text)
shap.plots.text(shap_values)

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


  0%|          | 0/72 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:11, 11.11s/it]               


**Generated Text** - "I am a data science student at Duke . I am interested in the "

Here, we can see that the generated token "role" is driven by "science", "student", and "at". The "interested" token is driven by the "data and "science" tokens from the input.

### Example 3: "It snowed in Durham today."

In [ ]:
input_text = ["It snowed in Durham today."]
tokenized_input = tokenizer(input_text, return_tensors="pt")
masker = shap.maskers.Text(tokenizer)
explainer = shap.Explainer(model, masker)
shap_values = explainer(input_text)
shap.plots.text(shap_values)

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


**Generated Text** - "It snow ed in Durham today . " I 'm not sure if it 's snow ing in"

Here, the "snowing" token is driven by the snow"ed" and "today" tokens from the input.

# Discussion

### Why SHAP Was Chosen
SHAP was selected for this analysis due to its unique strengths in providing interpretable explanations for complex machine learning models:
- **Local and Global Explanations:** SHAP offers both instance-specific (local) explanations and overall (global) insights into model behavior.
- **Model-Agnostic Approach:** SHAP can be applied to any machine learning model, including GPT-2, without requiring modifications to the model architecture.
- **Game-Theoretic Foundation:** SHAP is grounded in Shapley values from cooperative game theory, ensuring stability, fairness, and consistency in feature attributions.
- **Visualization Capabilities:** SHAP provides intuitive visualizations of token contributions, making it particularly suitable for NLP tasks like text generation.

### Strengths
- **Clear Insights:** SHAP allows us to pinpoint which input tokens contribute the most to specific predictions.
- **Additive Feature Attributions:** The sum of SHAP values aligns with the model's output, ensuring interpretability and transparency.
- **Token-Level Explanations:** For GPT-2, SHAP highlights how each input token influences the generation of specific output tokens.

### Limitations
- **Computational Complexity:** SHAP is computationally expensive, especially when applied to large models like GPT-2, as it requires evaluating multiple feature combinations.
- **Memory Intensive:** Explaining predictions for long sequences or large datasets can demand significant memory and processing power.

### Potential Improvements
- **Optimized SHAP Implementations:** Explore faster implementations of SHAP or limit the number of output tokens analyzed to reduce computational overhead.
- **Hybrid Techniques:** Combine SHAP with other explanation methods like Anchors to gain complementary insights (e.g., rule-based explanations).
- **Input Size Reduction:** Preprocess input text by truncating or summarizing it to focus on the most relevant parts for explanation.



# Conclusion

This notebook successfully demonstrated how SHAP can be used to explain predictions made by GPT-2. By analyzing the contributions of individual input tokens to specific output tokens, we gained valuable insights into how GPT-2 generates text.

### Findings
#### Example 1: Input - *"In a surprising discovery, scientists found evidence of life on Mars."*
GPT-2 generated the following output:  
*"In a surprising discovery , scientists found evidence of life on Mars . The discovery , reported in"*

1. For the generated token `"discovery"`:
   - The input tokens `"discovery"`, `"found"`, and `"of"` contributed the most to generating this word.
2. For the generated token `"reported"`:
   - The input tokens `"surprising"` and `"scientists"` had the highest contributions, while `"evidence"` and `"Mars"` contributed less.

#### Example 2: Input - *"I am a data science student at Duke."*
GPT-2 generated the following output:  
*"I am a data science student at Duke . I am interested in"*
1. For the generated token `"role"`:
   - The input tokens `"science"`, `"student"`, and `"at"` were key contributors.
2. For the generated token `"interested"`:
   - The input tokens `"data"` and `"science"` were the primary drivers.

#### Example 3: Input - *"It snowed in Durham today."*
GPT-2 generated the following output:
*"It snow ed in Durham today . " I 'm not sure if it 's snowing in"*
1. For the generated token `"snowing"`:
   - The input tokens `"snowed"` and `"today"` contributed significantly.

### Summary
SHAP provided meaningful explanations for GPT-2's predictions by highlighting token-level contributions. These insights can help debug models, improve interpretability, and build trust in AI systems. Future work could involve optimizing SHAP for large-scale NLP tasks or exploring additional explanation techniques for deeper insights.
